In [1]:
#Data Loading

import os
import scipy.io as sio

data_folder = './NASA dataset'
mat_files = [f for f in os.listdir(data_folder) if f.endswith(".mat")]

batteries = {}

for filename in mat_files:
    path = os.path.join(data_folder, filename)
    data = sio.loadmat(path, squeeze_me=True, struct_as_record=False)

    # Remove system keys
    keys = [k for k in data.keys() if not k.startswith("__")]

    # NASA files have only ONE useful variable (e.g., 'B0005')
    var_name = keys[0]  

    batteries[filename] = data[var_name]
    print(f" {filename} → structure loaded")

battery = next(iter(batteries.values()))
print("Loaded all files")

 B0005.mat → structure loaded
 B0006.mat → structure loaded
 B0007.mat → structure loaded
 B0018.mat → structure loaded
 B0025.mat → structure loaded
 B0026.mat → structure loaded
 B0027.mat → structure loaded
 B0028.mat → structure loaded
 B0029.mat → structure loaded
 B0030.mat → structure loaded
 B0031.mat → structure loaded
 B0032.mat → structure loaded
 B0033.mat → structure loaded
 B0034.mat → structure loaded
 B0036.mat → structure loaded
 B0038.mat → structure loaded
 B0039.mat → structure loaded
 B0040.mat → structure loaded
 B0041.mat → structure loaded
 B0042.mat → structure loaded
 B0043.mat → structure loaded
 B0044.mat → structure loaded
 B0045.mat → structure loaded
 B0046.mat → structure loaded
 B0047.mat → structure loaded
 B0048.mat → structure loaded
 B0049.mat → structure loaded
 B0050.mat → structure loaded
 B0051.mat → structure loaded
 B0052.mat → structure loaded
 B0053.mat → structure loaded
 B0054.mat → structure loaded
 B0055.mat → structure loaded
 B0056.mat

In [3]:
#first_cycle = battery.cycle[0]
#print(dir(first_cycle))
#print(dir(first_cycle.data))
#Above 3 commands are only to get idea of how data is structured. we have cycle fields containing (type → 'charge' / 'discharge' / 'impedance', time, ambient_temperature, data → contains actual measurements)
#inside cycle.data we have Voltage_measured, Current_measured, Temperature_measured, Voltage_charge, Current_charge, Time)
#battery has separate charge signals (Voltage_charge, Current_charge) but usually only Voltage_measured & Current_measured are used for degradation modeling



In [5]:
# Extract cycles + basic features into a DataFrame

import numpy as np
import pandas as pd

def extract_features(battery, name):
    rows = []

    for idx, cyc in enumerate(battery.cycle):
        d = cyc.data
        # Detect which fields exist 
        # Skip cycles with no voltage/current
        if hasattr(d, "Voltage_measured") and hasattr(d, "Current_measured"):
            V = np.array(d.Voltage_measured)
            I = np.array(d.Current_measured)

        elif hasattr(d, "Voltage_charge") and hasattr(d, "Current_charge"):
            V = np.array(d.Voltage_charge)
            I = np.array(d.Current_charge)

        else:
            # skip cycles with no useful data (impedance cycles)
            continue

        # Temperature 
        if hasattr(d, "Temperature_measured"):
            T = np.array(d.Temperature_measured)
        else:
            T = np.array([np.nan])

        #time (comment)
        if hasattr(d, "Time"): 
            t = np.array(d.Time)           
        else:
            t = np.nan

        # Capacity (only for discharge/reference cycles)
        if hasattr(d, "Capacity") and cyc.type.lower() == "discharge":
            cap = d.Capacity
        else:
            cap = np.nan

        # Store extracted features 
        row = {
            "battery": name,
            "cycle": idx,
            "V_min": V.min(),
            "V_max": V.max(),
            "V_mean": V.mean(),
            "I_min": I.min(), 
            "I_max": I.max(),
            "I_mean": I.mean(),
            "T_min": T.min(),
            "T_max": T.max(),
            "T_mean": T.mean(),
            "duration_s": t[-1]-t[0] if len(t)>1 else 0,
            "Capacity": cap
        }

        rows.append(row)

    return rows

all_rows = []

for filename, batt in batteries.items():
    simple_name = filename.replace(".mat", "")
    rows = extract_features(batt, simple_name)
    all_rows.extend(rows)


raw_df = pd.DataFrame(all_rows)
print(raw_df.head(20))
print(raw_df.shape)
print(f"Total rows loaded: {len(raw_df)}")

   battery  cycle     V_min     V_max    V_mean     I_min     I_max    I_mean  \
0    B0005      0  3.479394  4.209949  4.187420 -4.030268  1.514393  0.643455   
1    B0005      1  2.612467  4.191492  3.529829 -2.018015  0.000729 -1.818702   
2    B0005      2  3.001951  4.213016  4.058826 -3.361983  1.515178  0.949043   
3    B0005      3  2.587209  4.189773  3.537320 -2.016821  0.002927 -1.817560   
4    B0005      4  3.035879  4.212788  4.058139 -3.384408  1.516894  0.950529   
5    B0005      5  2.651917  4.188187  3.543737 -2.016574  0.001484 -1.816487   
6    B0005      6  3.066145  4.212924  4.058905 -3.412263  1.517503  0.952312   
7    B0005      7  2.592948  4.188461  3.543666 -2.015936  0.001547 -1.825589   
8    B0005      8  3.063766  4.212874  4.058330 -3.403625  1.516949  0.947728   
9    B0005      9  2.547420  4.188299  3.542343 -2.017426  0.001701 -1.826114   
10   B0005     10  3.059322  4.212764  4.059785 -3.394451  1.516510  0.932661   
11   B0005     11  2.520948 

In [7]:
df_clean = raw_df.copy()

# Ensure Capacity is numeric
df_clean['Capacity'] = pd.to_numeric(df_clean['Capacity'], errors='coerce')

# Interpolate Capacity linearly within each battery, , sorted by cycle
for b in df_clean['battery'].unique():
    temp = df_clean[df_clean['battery']==b].copy()
    temp['Capacity'] = temp['Capacity'].interpolate(method='linear')
    df_clean.loc[df_clean['battery']==b, 'Capacity'] = temp['Capacity']

# Quick check of capacity interpolation 
print(df_clean[['battery','cycle','Capacity']].head(350))


#batteries with first cycle as charge or impedance (as we gat nan capacity so not discharge) these values need to be filled
# below two lines show all batteries where Capacity is still NaN after interpolation i.e. those that had first cycle value as nan
#nan_capacity = df_clean[df_clean['Capacity'].isna()][['battery','cycle','Capacity']]
#print(nan_capacity)

# Fill first missing Capacity values within each battery using backward fill
df_clean['Capacity'] = df_clean.groupby('battery')['Capacity'].transform(lambda x: x.bfill())

#fill V/I/T/Voltage NaNs because these are measurement gaps
sensor_cols = ['V_min','V_max','V_mean', 'I_min','I_max', 'I_mean', 'T_min','T_max', 'T_mean', 'duration_s']

df_clean[sensor_cols] = (
    df_clean.groupby('battery')[sensor_cols]
            .transform(lambda x: x.ffill().bfill())
)
df_clean.isna().sum() #to check how many nans left



    battery  cycle  Capacity
0     B0005      0       NaN
1     B0005      1  1.856487
2     B0005      2  1.851407
3     B0005      3  1.846327
4     B0005      4  1.840838
..      ...    ...       ...
345   B0006      7  2.013285
346   B0006      8  2.006907
347   B0006      9  2.000528
348   B0006     10  2.007214
349   B0006     11  2.013899

[350 rows x 3 columns]


battery       0
cycle         0
V_min         0
V_max         0
V_mean        0
I_min         0
I_max         0
I_mean        0
T_min         0
T_max         0
T_mean        0
duration_s    0
Capacity      0
dtype: int64

In [10]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
df_clean


battery  cycle     V_min     V_max    V_mean     I_min         I_max  \
0      B0005      0  3.479394  4.209949  4.187420 -4.030268  1.514393e+00   
1      B0005      1  2.612467  4.191492  3.529829 -2.018015  7.285853e-04   
2      B0005      2  3.001951  4.213016  4.058826 -3.361983  1.515178e+00   
3      B0005      3  2.587209  4.189773  3.537320 -2.016821  2.927403e-03   
4      B0005      4  3.035879  4.212788  4.058139 -3.384408  1.516894e+00   
5      B0005      5  2.651917  4.188187  3.543737 -2.016574  1.483676e-03   
6      B0005      6  3.066145  4.212924  4.058905 -3.412263  1.517503e+00   
7      B0005      7  2.592948  4.188461  3.543666 -2.015936  1.547012e-03   
8      B0005      8  3.063766  4.212874  4.058330 -3.403625  1.516949e+00   
9      B0005      9  2.547420  4.188299  3.542343 -2.017426  1.701455e-03   
10     B0005     10  3.059322  4.212764  4.059785 -3.394451  1.516510e+00   
11     B0005     11  2.520948  4.188816  3.541335 -2.016235  2.489950e-03   
12     B0005     12  3.053360  4.213177  4.058914 -3.401390  1.514934e+00   
13     B0005     13  2.487927  4.188392  3.541025 -2.015833  2.314296e-03   
14     B0005     14  3.048721  4.212851  4.053426 -3.385806  1.516038e+00   
15     B0005     15  2.665205  4.188928  3.554133 -2.016640  2.227616e-03   
16     B0005     16  3.082422  4.213142  4.055638 -3.433870  1.517392e+00   
17     B0005     17  2.603858  4.189029  3.552936 -2.018357  5.401028e-03   
18     B0005     18  3.075796  4.212950  4.055139 -3.416544  1.517755e+00   
19     B0005     19  2.552854  4.189223  3.551206 -2.016072  3.019148e-03   
20     B0005     20  3.069853  4.213227  4.054492 -3.421771  1.516046e+00   
21     B0005     21  2.472448  4.188916  3.549292 -2.016071  2.626400e-03   
22     B0005     22  3.061259  4.212826  4.052615 -3.404491  1.516932e+00   
23     B0005     23  3.341571  4.212864  4.076087 -3.783890  1.517756e+00   
24     B0005     24  2.649564  4.189876  3.559759 -2.016852  2.364524e-03   
25     B0005     25  3.092616  4.212725  4.054613 -3.438089  1.518731e+00   
26     B0005     26  2.572498  4.189287  3.558082 -2.016394  1.858379e-03   
27     B0005     27  3.082964  4.213058  4.059266 -3.433445  1.516641e+00   
28     B0005     28  2.524989  4.188838  3.555692 -2.015812  2.266465e-03   
29     B0005     29  3.077082  4.213191  4.053495 -3.432002  1.516969e+00   
30     B0005     30  2.694622  4.189110  3.562747 -2.019351  1.319946e-03   
31     B0005     31  3.109982  4.212769  4.057010 -3.482051  1.515519e+00   
32     B0005     32  2.640101  4.189212  3.561452 -2.016442  3.078253e-03   
33     B0005     33  3.105446  4.212911  4.056509 -3.479010  1.517095e+00   
34     B0005     34  2.573904  4.188900  3.560342 -2.016465  9.018486e-04   
35     B0005     35  3.098521  4.213175  4.055992 -3.461447  1.516463e+00   
36     B0005     36  2.494240  4.188780  3.559119 -2.018107 -4.481240e-04   
37     B0005     37  3.089171  4.212973  4.056478 -3.450379  1.516116e+00   
38     B0005     38  2.455679  4.189273  3.557887 -2.017025  2.337559e-03   
39     B0005     39  3.235784  4.212806  4.079851 -3.646980  1.516732e+00   
40     B0005     41  2.632143  4.187614  3.552038 -2.016847  5.955166e-03   
41     B0005     43  3.068369  4.213442  4.057904 -3.398837  1.515326e+00   
42     B0005     45  2.502776  4.187629  3.552567 -2.016191  1.618264e-03   
43     B0005     47  3.062345  4.212832  4.056384 -3.407889  1.516711e+00   
44     B0005     49  2.617508  4.187447  3.556794 -2.016760  2.519216e-03   
45     B0005     51  3.090414  4.212770  4.058279 -3.464130  1.516315e+00   
46     B0005     53  2.694074  4.187344  3.561410 -2.016023  3.793312e-03   
47     B0005     55  3.114013  4.213277  4.065739 -3.493557  1.516999e+00   
48     B0005     57  2.623767  4.187438  3.556611 -2.017191  3.438889e-03   
49     B0005     59  3.108464  4.212690  4.061150 -3.495101  1.518474e+00   
50     B0005     61  2.501080  4.187741  3.558674 -2.016115  1.261442e-03   
5

In [11]:
df_clean.isna().sum() #to check how many nans left

battery       0
cycle         0
V_min         0
V_max         0
V_mean        0
I_min         0
I_max         0
I_mean        0
T_min         0
T_max         0
T_mean        0
duration_s    0
Capacity      0
dtype: int64

In [16]:
nominal_capacity = 2

# Compute SOH as percentage
df_clean['SOH'] = df_clean['Capacity'] / nominal_capacity * 100
df_clean

battery  cycle     V_min     V_max    V_mean     I_min         I_max  \
0      B0005      0  3.479394  4.209949  4.187420 -4.030268  1.514393e+00   
1      B0005      1  2.612467  4.191492  3.529829 -2.018015  7.285853e-04   
2      B0005      2  3.001951  4.213016  4.058826 -3.361983  1.515178e+00   
3      B0005      3  2.587209  4.189773  3.537320 -2.016821  2.927403e-03   
4      B0005      4  3.035879  4.212788  4.058139 -3.384408  1.516894e+00   
5      B0005      5  2.651917  4.188187  3.543737 -2.016574  1.483676e-03   
6      B0005      6  3.066145  4.212924  4.058905 -3.412263  1.517503e+00   
7      B0005      7  2.592948  4.188461  3.543666 -2.015936  1.547012e-03   
8      B0005      8  3.063766  4.212874  4.058330 -3.403625  1.516949e+00   
9      B0005      9  2.547420  4.188299  3.542343 -2.017426  1.701455e-03   
10     B0005     10  3.059322  4.212764  4.059785 -3.394451  1.516510e+00   
11     B0005     11  2.520948  4.188816  3.541335 -2.016235  2.489950e-03   
12     B0005     12  3.053360  4.213177  4.058914 -3.401390  1.514934e+00   
13     B0005     13  2.487927  4.188392  3.541025 -2.015833  2.314296e-03   
14     B0005     14  3.048721  4.212851  4.053426 -3.385806  1.516038e+00   
15     B0005     15  2.665205  4.188928  3.554133 -2.016640  2.227616e-03   
16     B0005     16  3.082422  4.213142  4.055638 -3.433870  1.517392e+00   
17     B0005     17  2.603858  4.189029  3.552936 -2.018357  5.401028e-03   
18     B0005     18  3.075796  4.212950  4.055139 -3.416544  1.517755e+00   
19     B0005     19  2.552854  4.189223  3.551206 -2.016072  3.019148e-03   
20     B0005     20  3.069853  4.213227  4.054492 -3.421771  1.516046e+00   
21     B0005     21  2.472448  4.188916  3.549292 -2.016071  2.626400e-03   
22     B0005     22  3.061259  4.212826  4.052615 -3.404491  1.516932e+00   
23     B0005     23  3.341571  4.212864  4.076087 -3.783890  1.517756e+00   
24     B0005     24  2.649564  4.189876  3.559759 -2.016852  2.364524e-03   
25     B0005     25  3.092616  4.212725  4.054613 -3.438089  1.518731e+00   
26     B0005     26  2.572498  4.189287  3.558082 -2.016394  1.858379e-03   
27     B0005     27  3.082964  4.213058  4.059266 -3.433445  1.516641e+00   
28     B0005     28  2.524989  4.188838  3.555692 -2.015812  2.266465e-03   
29     B0005     29  3.077082  4.213191  4.053495 -3.432002  1.516969e+00   
30     B0005     30  2.694622  4.189110  3.562747 -2.019351  1.319946e-03   
31     B0005     31  3.109982  4.212769  4.057010 -3.482051  1.515519e+00   
32     B0005     32  2.640101  4.189212  3.561452 -2.016442  3.078253e-03   
33     B0005     33  3.105446  4.212911  4.056509 -3.479010  1.517095e+00   
34     B0005     34  2.573904  4.188900  3.560342 -2.016465  9.018486e-04   
35     B0005     35  3.098521  4.213175  4.055992 -3.461447  1.516463e+00   
36     B0005     36  2.494240  4.188780  3.559119 -2.018107 -4.481240e-04   
37     B0005     37  3.089171  4.212973  4.056478 -3.450379  1.516116e+00   
38     B0005     38  2.455679  4.189273  3.557887 -2.017025  2.337559e-03   
39     B0005     39  3.235784  4.212806  4.079851 -3.646980  1.516732e+00   
40     B0005     41  2.632143  4.187614  3.552038 -2.016847  5.955166e-03   
41     B0005     43  3.068369  4.213442  4.057904 -3.398837  1.515326e+00   
42     B0005     45  2.502776  4.187629  3.552567 -2.016191  1.618264e-03   
43     B0005     47  3.062345  4.212832  4.056384 -3.407889  1.516711e+00   
44     B0005     49  2.617508  4.187447  3.556794 -2.016760  2.519216e-03   
45     B0005     51  3.090414  4.212770  4.058279 -3.464130  1.516315e+00   
46     B0005     53  2.694074  4.187344  3.561410 -2.016023  3.793312e-03   
47     B0005     55  3.114013  4.213277  4.065739 -3.493557  1.516999e+00   
48     B0005     57  2.623767  4.187438  3.556611 -2.017191  3.438889e-03   
49     B0005     59  3.108464  4.212690  4.061150 -3.495101  1.518474e+00   
50     B0005     61  2.501080  4.187741  3.558674 -2.016115  1.261442e-03   
5

In [18]:
# Save the cleaned dataframe
df_clean.to_csv('df_clean.csv', index=False)

In [20]:
# ADDING output target RUL COLUMN (Threshold = 80% SOH) 

# 1. Identify the cycle where SOH hits 80% for each battery
# Identify rows where SOH hits 80% (i.e. SOH <= 80) for each battery, then take the minimum cycle number for each battery as EOL cycle.
EoL_threshold_SoH = 80

# Find batteries that reach the threshold
complete_batteries = df_clean.groupby('battery')['SOH'].min()
complete_batteries = complete_batteries[complete_batteries <= EoL_threshold_SoH].index.tolist()

# Filter dataframe
df_complete = df_clean[df_clean['battery'].isin(complete_batteries)].copy()
print(f"Using {len(complete_batteries)} complete batteries for RUL prediction.")

# Find the specific cycle number where each battery "failed" i.e. SOH ≤ threshold (EOL cycle)
eol_cycles = df_complete[df_complete["SOH"] <= EoL_threshold_SoH].groupby("battery")["cycle"].min()

# Map EOL cycle back
df_complete["EOL_cycle"] = df_complete["battery"].map(eol_cycles)

# Compute RUL
df_complete["RUL"] = df_complete["EOL_cycle"] - df_complete["cycle"]
df_complete = df_complete[df_complete["RUL"] >= 0].reset_index(drop=True)

df_complete.to_csv("df_complete_with_rul.csv", index=False)
print("RUL column added for complete batteries only.")


Using 28 complete batteries for RUL prediction.
RUL column added for complete batteries only.
